In [1]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
import mysql.connector
import pandas as pd
import json

In [3]:
def open_database():
    con = mysql.connector.connect(user='dbadmin', password='washywashy',host='127.0.0.1',database='tests')
    return con, con.cursor()

def read_csv(filename):
    df = pd.read_csv(filename, low_memory=False)
    return df

def select_columns(df, columns):
    return df[columns]

def get_data():
    df = read_csv('./data/movies_imbd.csv')
    return df

def get_column_df(col):
    df = read_csv('./data/movies_imbd.csv')
    df = select_columns(df,[col])
    df = df[~pd.isnull(df[col])]
    df.fillna("",inplace=True)
    return df

def from_key_to_key(s, fk, tk):
    fp = s.find("'"+fk+"':")
    tp = s.find("'"+tk+"':")    
    return s[fp+len(fk)+4:tp-2]

def get_single_id_name(s):
    return from_key_to_key(s, "id", "name"), from_key_to_key(s, "name", "poster_path")

In [3]:
# Production Countries

def get_production_countries_data():
    df = get_column_df('production_countries')
    production_countries = {}
    for c in df.values:
        if (c[0] != '[]'):
            lines = c[0].split('},')
            for l in lines:
                l = l.replace("[{'iso_3166_1","{'iso_3166_1").replace("}]","}")

                if l[-1] != "}":
                    l = l + "}"
                l = l.strip()

                fp = l.find("'"+'iso_3166_1'+"':")
                tp = l.find(""+'name'+"")
                initials = l[fp+len('iso_3166_1')+5:tp-4]

    #           getting country was different
                fp = l.find("'"+'name'+"':")
                tp = l.find(""+'}'+"")
                country = l[fp+len('name')+5:tp-1]

                production_countries[initials] = country

    return production_countries   

def create_production_countries_table():
    con, cursor = open_database()
    cursor.execute("drop table if exists tests.production_countries")
    create_table_sql = """
        create table tests.production_countries (
            id int not null auto_increment,
            initials varchar(10),
            name varchar(250),
            primary key(id)
        )
        """
    cursor.execute(create_table_sql)
    con.commit()    
    con.close()
    
def insert_into_production_countries():
    pc = get_production_countries_data()
    values = []
    for key in pc:
        values.append((key,pc[key]))
    con, cursor = open_database()
    cursor.executemany("insert into tests.production_countries (initials, name) values (%s, %s)", values)
    con.commit()    
    con.close()        

In [4]:
# create_production_countries_table()
# insert_into_production_countries()

In [17]:
# Genres 

def get_genres_data():
    genres={}
    df = get_column_df('genres')
    for s in df.values:
            if (s[0] != '[]'):
                parts = s[0].split('},')        
                for p in parts:
                    p = p.replace("[{'id","{'id").replace(" {'id'", "{'id'").replace("}]", "}").replace("} ", "}")
                    p = p.replace("[{'name","{'name")
                    if p[-1] != '}':
                        p = p + "}"
                    p = p.replace("'", '"')
                    obj = json.loads(p)

                    id = obj['id']
                    name = obj['name']
                    genres[id] = name
    return genres                    

def create_table_genres():
    con, cursor = open_database()
    cursor.execute("drop table if exists tests.genres")
    create_table_sql = """
    create table tests.genres (
        id int,
        name varchar(512),
        primary key(id)
    )
    """
    cursor.execute(create_table_sql)
    con.commit()    
    con.close()

def insert_into_genres():
    gens = get_genres_data()
    values = []
    for key in gens:
        values.append((key,gens[key]))
    con, cursor = open_database()
    cursor.executemany("insert into tests.genres (id, name) values (%s, %s)", values)
    con.commit()    
    con.close()     

In [6]:
# create_table_genres()
# insert_into_genres()

In [7]:
# Production Companies

def get_production_companies_data():
    production_companies = {}
    df = get_column_df('production_companies')
    for c in df.sample(1000).values:
        if(c[0] != '[]'):
            parts = c[0].split('},')        
            for p in parts:
                p = p.replace("[{'id","{'id").replace(" {'id'", "{'id'").replace("}]", "}").replace("} ", "}")
                p = p.replace("[{'name","{'name")
                if p[-1] != '}':
                    p = p + "}"
                    p = p.replace("{'name': ", "").replace("'id': ", "").replace('}', '')        
                    parts2 = p.split("', ")
                    if len(parts2) == 2:
                        name = parts2[0].strip()[1:]
                        id = parts2[1]
                        production_companies[id] = name
                    else:
                        parts2 = p.split('", ')
                        name = parts2[0].strip()[1:]
                        id = parts2[1]
                        production_companies[id] = name
    return production_companies


def create_production_companies_table():
    con, cursor = open_database()
    cursor.execute("drop table if exists tests.production_companies")
    create_table_sql = """
    create table tests.production_companies (
        id int,
        name varchar(512),
        primary key(id)
    )
    """
    cursor.execute(create_table_sql)
    con.commit()    
    con.close()
    
def insert_production_companies_data():
    pc = get_production_companies_data()
    values = []
    for key in pc:
        values.append((key, pc[key]))
    con, cursor = open_database()
    cursor.executemany("insert into production_companies (id, name) values (%s, %s)", values)
    con.commit()    
    con.close()    

In [8]:
# create_production_companies_table()
# insert_production_companies_data()

In [9]:
# collection Belonging

def get_collection_data():
    df = get_column_df("belongs_to_collection")
    collection_belonging = {}
    for s in df.values:
        s = s[0]
        
        id = from_key_to_key(s,'id','name')        
        name = from_key_to_key(s,'name','poster_path')
        name = name.replace("'", "").replace('"', '')
        if id != '' and name != '':
            collection_belonging[id] = name
        
    return collection_belonging
    
def create_collection_table():
    con, cursor = open_database()
   

In [10]:
# create_collection_table()
# insert_into_collection_table()

In [21]:
get_genres_data()


{16: 'Animation',
 35: 'Comedy',
 10751: 'Family',
 12: 'Adventure',
 14: 'Fantasy',
 10749: 'Romance',
 18: 'Drama',
 28: 'Action',
 80: 'Crime',
 53: 'Thriller',
 27: 'Horror',
 36: 'History',
 878: 'Science Fiction',
 9648: 'Mystery',
 10752: 'War',
 10769: 'Foreign',
 10402: 'Music',
 99: 'Documentary',
 37: 'Western',
 10770: 'TV Movie',
 11176: 'Carousel Productions',
 11602: 'Vision View Entertainment',
 29812: 'Telescene Film Group Productions',
 2883: 'Aniplex',
 7759: 'GoHands',
 7760: 'BROSTA TV',
 7761: 'Mardock Scramble Production Committee',
 33751: 'Sentai Filmworks',
 17161: 'Odyssey Media',
 18012: 'Pulser Productions',
 18013: 'Rogue State',
 23822: 'The Cartel'}

In [23]:
df = read_csv('./data/movies_imbd.csv')
df = select_columns(df, ['genres','id'])

for x in df.values:
    print(x)
    


["[{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]"
 '862']
["[{'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}, {'id': 10751, 'name': 'Family'}]"
 '8844']
["[{'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}]"
 '15602']
["[{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]"
 '31357']
["[{'id': 35, 'name': 'Comedy'}]" '11862']
["[{'id': 28, 'name': 'Action'}, {'id': 80, 'name': 'Crime'}, {'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}]"
 '949']
["[{'id': 35, 'name': 'Comedy'}, {'id': 10749, 'name': 'Romance'}]"
 '11860']
["[{'id': 28, 'name': 'Action'}, {'id': 12, 'name': 'Adventure'}, {'id': 18, 'name': 'Drama'}, {'id': 10751, 'name': 'Family'}]"
 '45325']
["[{'id': 28, 'name': 'Action'}, {'id': 12, 'name': 'Adventure'}, {'id': 53, 'name': 'Thriller'}]"
 '9091']
["[{'id': 12, 'name': 'Adventure'}, {'id': 28, 'name': 'Action'}, {'id': 53, 'name': 'Thriller'}]

["[{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]" '10818']
["[{'id': 27, 'name': 'Horror'}]" '14456']
["[{'id': 18, 'name': 'Drama'}]" '15840']
["[{'id': 18, 'name': 'Drama'}]" '15830']
["[{'id': 80, 'name': 'Crime'}, {'id': 18, 'name': 'Drama'}]" '25647']
["[{'id': 53, 'name': 'Thriller'}, {'id': 80, 'name': 'Crime'}, {'id': 18, 'name': 'Drama'}]"
 '14898']
["[{'id': 53, 'name': 'Thriller'}, {'id': 35, 'name': 'Comedy'}]" '12416']
["[{'id': 27, 'name': 'Horror'}, {'id': 9648, 'name': 'Mystery'}, {'id': 53, 'name': 'Thriller'}]"
 '572']
["[{'id': 53, 'name': 'Thriller'}, {'id': 18, 'name': 'Drama'}]" '36226']
["[{'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}, {'id': 10769, 'name': 'Foreign'}]"
 '60531']
["[{'id': 35, 'name': 'Comedy'}, {'id': 10749, 'name': 'Romance'}]"
 '13021']
["[{'id': 14, 'name': 'Fantasy'}, {'id': 9648, 'name': 'Mystery'}, {'id': 53, 'name': 'Thriller'}]"
 '16007']
["[{'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}, {'i

["[{'id': 35, 'name': 'Comedy'}]" '290274']
["[{'id': 10402, 'name': 'Music'}, {'id': 99, 'name': 'Documentary'}, {'id': 18, 'name': 'Drama'}, {'id': 35, 'name': 'Comedy'}]"
 '75785']
["[{'id': 99, 'name': 'Documentary'}]" '123561']
["[{'id': 18, 'name': 'Drama'}]" '95372']
["[{'id': 27, 'name': 'Horror'}, {'id': 9648, 'name': 'Mystery'}, {'id': 53, 'name': 'Thriller'}]"
 '265010']
["[{'id': 53, 'name': 'Thriller'}, {'id': 18, 'name': 'Drama'}]" '157823']
["[{'id': 28, 'name': 'Action'}, {'id': 80, 'name': 'Crime'}]" '31937']
['[]' '176069']
["[{'id': 53, 'name': 'Thriller'}, {'id': 18, 'name': 'Drama'}]" '85765']
["[{'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}]" '82760']
["[{'id': 28, 'name': 'Action'}, {'id': 37, 'name': 'Western'}]" '44022']
["[{'id': 28, 'name': 'Action'}, {'id': 37, 'name': 'Western'}]" '32142']
['[]' '360380']
["[{'id': 18, 'name': 'Drama'}, {'id': 27, 'name': 'Horror'}, {'id': 53, 'name': 'Thriller'}]"
 '211065']
["[{'id': 18, 'name': 'Drama'}]" '

["[{'id': 99, 'name': 'Documentary'}]" '78282']
["[{'id': 99, 'name': 'Documentary'}]" '268669']
["[{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}, {'id': 10769, 'name': 'Foreign'}]"
 '28527']
["[{'id': 28, 'name': 'Action'}, {'id': 10749, 'name': 'Romance'}]"
 '347317']
["[{'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}, {'id': 18, 'name': 'Drama'}]"
 '41228']
["[{'id': 18, 'name': 'Drama'}]" '16010']
["[{'id': 53, 'name': 'Thriller'}, {'id': 878, 'name': 'Science Fiction'}, {'id': 18, 'name': 'Drama'}]"
 '106669']
["[{'id': 18, 'name': 'Drama'}, {'id': 10769, 'name': 'Foreign'}]" '85087']
["[{'id': 10402, 'name': 'Music'}]" '238436']
["[{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}, {'id': 14, 'name': 'Fantasy'}]"
 '90034']
['[]' '192480']
['[]' '172973']
["[{'id': 16, 'name': 'Animation'}, {'id': 10751, 'name': 'Family'}]"
 '90319']
["[{'id': 16, 'name': 'Animation'}, {'id